In [1]:
import os
os.chdir("/home/atulgang/Thesis")


In [2]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [3]:
import nltk
from nltk.tokenize import word_tokenize
from stop_words import get_stop_words
from nltk.stem import WordNetLemmatizer
from gensim import corpora, models
import gensim
import glob2
from itertools import chain
import os
import numpy as np
import itertools
import cPickle as pickle
from  scipy.stats import rankdata
import copy
from openpyxl import Workbook
from openpyxl.compat import range
from openpyxl.utils import get_column_letter
from openpyxl import load_workbook
import pandas as pd
from scipy.stats import hmean
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk import pos_tag
from nltk.stem import WordNetLemmatizer

2018-05-04 15:57:21,889 : INFO : 'pattern' package not found; tag filters are not available for English


In [4]:

# WordNet only cares about 5 parts of speech.
# The other parts of speech will be tagged as nouns.

part = {
    'N' : 'n',
    'V' : 'v',
    'J' : 'a',
    'S' : 's',
    'R' : 'r'
}

wnl = WordNetLemmatizer()

def convert_tag(penn_tag):
    '''
    convert_tag() accepts the **first letter** of a Penn part-of-speech tag,
    then uses a dict lookup to convert it to the appropriate WordNet tag.
    '''
    if penn_tag in part.keys():
        return part[penn_tag]
    else:
        # other parts of speech will be tagged as nouns
        return 'n'


def tag_and_lem(element):
    '''
    tag_and_lem() accepts a token list, tags, converts tags,
    lemmatizes, and returns a string
    '''
    # list of tuples [('token', 'tag'), ('token2', 'tag2')...]
    sent = pos_tag(element) # must tag in context
    return [ wnl.lemmatize(sent[k][0], convert_tag(sent[k][1][0])) for k in range(len(sent))]

In [5]:
# ignores everything except english alphabet and  
def only_alphabet(text):
    return ''.join(i for i in text if (ord(i)<123 and ord(i)>96) or (ord(i)<91 and ord(i)>64) or ord(i)==32) 

full_filenames = []
x= ['LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt','LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt' ,'LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt']
for glob_filenames in x:
    glob_filenames = os.path.normpath(glob_filenames)
    for filename in sorted(glob2.glob(glob_filenames)):
        full_filenames.append(filename)
            
filenames = []
x= ['LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt','LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt' ,'LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt']
for glob_filenames in x:
    glob_filenames = os.path.normpath(glob_filenames)
    for filename in sorted(glob2.glob(glob_filenames)):
        filenames.append(os.path.basename(filename))

In [6]:
en_stop = set(get_stop_words('en'))

# "yield" for each file return token list  i.e list of lists
def files_to_tokens(glob_filenames):
    glob_filenames = os.path.normpath(glob_filenames)
    for filename in sorted(glob2.glob(glob_filenames)):
        f = open(filename)
        #print filename
        # read the whole file as lowercase string
        string = (f.read()).lower()
        try:
            temp = word_tokenize(string)
        except:
            string = string.decode("latin-1")
            temp = word_tokenize(string)
        
        tokens = []
        # tokenize that string
        for word in temp:
            w =  only_alphabet(word).lower()
            if w not in en_stop:
                if w:
                    tokens.append(w)
        tokens = tag_and_lem(tokens)
        yield tokens
        f.close()

        
# yields token list for files specific to courts; needed for creating dictionaries
class texts:
    def DCDRC(self):
        return files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/**/*.txt')
    def NCDRC(self):
        return files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt')
    def SCDRC(self):
        return files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt')
    def DelhiHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt')
    def JharkhandHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt')
    def JodhpurHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt')
    def KolkataHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt')
    def SupremeCourt(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt')
    def everything(self):
        return chain(self.DCDRC(), self.NCDRC(), self.SCDRC(), self.DelhiHC(),
                     self.JharkhandHC(), self.JodhpurHC(), self.KolkataHC(), self.SupremeCourt())

# yields bow for each file - tuples id,fq ; needed to train models   
class my_corpus:    
    def DCDRC(self):
        for text in files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/*.txt'):
            yield dictionary.doc2bow(text)
    def NCDRC(self):
        for text in files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt'):
            yield dictionary.doc2bow(text)            
    def SCDRC(self):
        for text in files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def DelhiHC(self):
        for text in files_to_tokens('LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def JharkhandHC(self):
        for text in files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def JodhpurHC(self):
        for text in  files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def KolkataHC(self):
        for text in  files_to_tokens('LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def SupremeCourt(self):
        for text in  files_to_tokens('LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt'):
            yield dictionary.doc2bow(text)
    def everything(self):
        return chain(self.DCDRC(), self.NCDRC(), self.SCDRC(), self.DelhiHC(),
                     self.JharkhandHC(), self.JodhpurHC(), self.KolkataHC(), self.SupremeCourt())
        
        

In [7]:
#################################### laod the dictinary
dictionary = corpora.Dictionary.load('dict/lem10')

2018-05-04 15:57:39,555 : INFO : loading Dictionary object from dict/lem10
2018-05-04 15:57:39,616 : INFO : loaded dict/lem10


In [8]:
######################################## load BOW
corpus = corpora.MmCorpus('corpus/bow_lem10.mm')

2018-05-04 15:57:39,738 : INFO : loaded corpus index from corpus/bow_lem10.mm.index
2018-05-04 15:57:39,738 : INFO : initializing cython corpus reader from corpus/bow_lem10.mm
2018-05-04 15:57:39,739 : INFO : accepted corpus with 351985 documents, 169716 features, 99651009 non-zero entries


In [9]:
# %%time

# c = texts()
# count = 0
# for x in c.everything():
#     x = [ i for i in x if i in dictionary.token2id]
#     with open(os.path.normpath('Token_corpus2/' + str(count)), 'wb') as fp:
#         pickle.dump(x, fp)
#     count=count+1


In [10]:
def token_corpus(i):
    with open (os.path.normpath('Token_corpus2/' + str(i)), 'rb') as fp:
            itemlist = pickle.load(fp)
            return itemlist   

In [11]:
class iter_token_corpus:
    def __iter__(self):
        for i in xrange(0, 351985):
            with open (os.path.normpath('Token_corpus2/' + str(i)), 'rb') as fp:
                itemlist = pickle.load(fp)
                yield itemlist

In [12]:
%%time
model = gensim.models.fasttext.FastText(iter_token_corpus(), hs = 1, size=300, iter = 20, min_count=0, sample=.00001, workers=8)

2018-05-04 15:57:47,401 : INFO : collecting all words and their counts
2018-05-04 15:57:47,404 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2018-05-04 15:58:01,667 : INFO : PROGRESS: at sentence #10000, processed 12250127 words, keeping 69492 word types
2018-05-04 15:58:14,712 : INFO : PROGRESS: at sentence #20000, processed 23019662 words, keeping 93100 word types
2018-05-04 15:58:24,954 : INFO : PROGRESS: at sentence #30000, processed 33121221 words, keeping 108174 word types
2018-05-04 15:58:33,524 : INFO : PROGRESS: at sentence #40000, processed 41771479 words, keeping 121160 word types
2018-05-04 15:58:40,333 : INFO : PROGRESS: at sentence #50000, processed 48600564 words, keeping 127318 word types
2018-05-04 15:58:47,010 : INFO : PROGRESS: at sentence #60000, processed 54839174 words, keeping 133012 word types
2018-05-04 15:58:53,139 : INFO : PROGRESS: at sentence #70000, processed 60283301 words, keeping 136653 word types
2018-05-04 15:59:00,128 : I

2018-05-04 16:03:48,168 : INFO : EPOCH 1 - PROGRESS: at 0.78% examples, 23641 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:49,351 : INFO : EPOCH 1 - PROGRESS: at 0.83% examples, 23546 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:50,379 : INFO : EPOCH 1 - PROGRESS: at 0.85% examples, 23578 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:51,484 : INFO : EPOCH 1 - PROGRESS: at 0.87% examples, 23424 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:52,590 : INFO : EPOCH 1 - PROGRESS: at 0.91% examples, 23593 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:53,593 : INFO : EPOCH 1 - PROGRESS: at 0.92% examples, 23539 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:54,830 : INFO : EPOCH 1 - PROGRESS: at 0.94% examples, 23438 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:56,071 : INFO : EPOCH 1 - PROGRESS: at 0.98% examples, 23425 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:03:57,198 : INFO : EPOCH 1 - PROGRESS: at 1.02% examples, 23615 words/s, in_qsize 0, out_qsize 0
2

2018-05-04 16:05:09,004 : INFO : EPOCH 1 - PROGRESS: at 2.23% examples, 24417 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:05:10,096 : INFO : EPOCH 1 - PROGRESS: at 2.25% examples, 24443 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:05:11,318 : INFO : EPOCH 1 - PROGRESS: at 2.28% examples, 24377 words/s, in_qsize 2, out_qsize 1
2018-05-04 16:05:12,418 : INFO : EPOCH 1 - PROGRESS: at 2.32% examples, 24518 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:05:13,730 : INFO : EPOCH 1 - PROGRESS: at 2.41% examples, 24472 words/s, in_qsize 2, out_qsize 0
2018-05-04 16:05:14,910 : INFO : EPOCH 1 - PROGRESS: at 2.44% examples, 24536 words/s, in_qsize 0, out_qsize 1
2018-05-04 16:05:15,958 : INFO : EPOCH 1 - PROGRESS: at 2.46% examples, 24545 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:05:16,962 : INFO : EPOCH 1 - PROGRESS: at 2.48% examples, 24521 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:05:18,162 : INFO : EPOCH 1 - PROGRESS: at 2.51% examples, 24494 words/s, in_qsize 0, out_qsize 1
2

2018-05-04 16:06:31,042 : INFO : EPOCH 1 - PROGRESS: at 3.99% examples, 24649 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:32,098 : INFO : EPOCH 1 - PROGRESS: at 4.02% examples, 24617 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:33,123 : INFO : EPOCH 1 - PROGRESS: at 4.05% examples, 24620 words/s, in_qsize 4, out_qsize 0
2018-05-04 16:06:34,140 : INFO : EPOCH 1 - PROGRESS: at 4.07% examples, 24641 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:35,218 : INFO : EPOCH 1 - PROGRESS: at 4.09% examples, 24661 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:36,327 : INFO : EPOCH 1 - PROGRESS: at 4.11% examples, 24681 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:37,346 : INFO : EPOCH 1 - PROGRESS: at 4.12% examples, 24676 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:38,694 : INFO : EPOCH 1 - PROGRESS: at 4.14% examples, 24657 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:06:39,830 : INFO : EPOCH 1 - PROGRESS: at 4.17% examples, 24670 words/s, in_qsize 0, out_qsize 0
2

2018-05-04 16:07:53,119 : INFO : EPOCH 1 - PROGRESS: at 5.87% examples, 24560 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:07:54,200 : INFO : EPOCH 1 - PROGRESS: at 5.89% examples, 24552 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:07:55,278 : INFO : EPOCH 1 - PROGRESS: at 5.91% examples, 24549 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:07:56,315 : INFO : EPOCH 1 - PROGRESS: at 5.95% examples, 24580 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:07:57,324 : INFO : EPOCH 1 - PROGRESS: at 5.98% examples, 24608 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:07:58,350 : INFO : EPOCH 1 - PROGRESS: at 6.02% examples, 24619 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:07:59,457 : INFO : EPOCH 1 - PROGRESS: at 6.06% examples, 24617 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:08:00,510 : INFO : EPOCH 1 - PROGRESS: at 6.09% examples, 24637 words/s, in_qsize 0, out_qsize 0
2018-05-04 16:08:01,570 : INFO : EPOCH 1 - PROGRESS: at 6.12% examples, 24647 words/s, in_qsize 0, out_qsize 0
2

...

2018-05-05 06:50:59,902 : INFO : EPOCH 20 - PROGRESS: at 93.89% examples, 42559 words/s, in_qsize 0, out_qsize 1
2018-05-05 06:51:00,980 : INFO : EPOCH 20 - PROGRESS: at 93.90% examples, 42556 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:51:02,014 : INFO : EPOCH 20 - PROGRESS: at 93.92% examples, 42560 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:51:03,054 : INFO : EPOCH 20 - PROGRESS: at 93.94% examples, 42561 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:51:04,073 : INFO : EPOCH 20 - PROGRESS: at 93.96% examples, 42561 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:51:05,126 : INFO : EPOCH 20 - PROGRESS: at 93.98% examples, 42561 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:51:06,137 : INFO : EPOCH 20 - PROGRESS: at 94.00% examples, 42560 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:51:07,248 : INFO : EPOCH 20 - PROGRESS: at 94.02% examples, 42563 words/s, in_qsize 0, out_qsize 1
2018-05-05 06:51:08,429 : INFO : EPOCH 20 - PROGRESS: at 94.04% examples, 42561 words/s, in_qsiz

2018-05-05 06:52:17,418 : INFO : EPOCH 20 - PROGRESS: at 95.88% examples, 42634 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:52:18,406 : INFO : EPOCH 20 - PROGRESS: at 95.91% examples, 42634 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:52:19,430 : INFO : EPOCH 20 - PROGRESS: at 95.95% examples, 42638 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:52:20,438 : INFO : EPOCH 20 - PROGRESS: at 95.98% examples, 42640 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:52:21,506 : INFO : EPOCH 20 - PROGRESS: at 96.01% examples, 42637 words/s, in_qsize 0, out_qsize 2
2018-05-05 06:52:22,522 : INFO : EPOCH 20 - PROGRESS: at 96.04% examples, 42636 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:52:23,610 : INFO : EPOCH 20 - PROGRESS: at 96.06% examples, 42623 words/s, in_qsize 2, out_qsize 0
2018-05-05 06:52:24,625 : INFO : EPOCH 20 - PROGRESS: at 96.08% examples, 42636 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:52:25,647 : INFO : EPOCH 20 - PROGRESS: at 96.11% examples, 42640 words/s, in_qsiz

2018-05-05 06:53:34,118 : INFO : EPOCH 20 - PROGRESS: at 97.85% examples, 42638 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:35,123 : INFO : EPOCH 20 - PROGRESS: at 97.89% examples, 42639 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:36,176 : INFO : EPOCH 20 - PROGRESS: at 97.92% examples, 42640 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:37,178 : INFO : EPOCH 20 - PROGRESS: at 97.95% examples, 42641 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:38,279 : INFO : EPOCH 20 - PROGRESS: at 97.99% examples, 42639 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:39,290 : INFO : EPOCH 20 - PROGRESS: at 98.04% examples, 42639 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:40,367 : INFO : EPOCH 20 - PROGRESS: at 98.08% examples, 42640 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:41,394 : INFO : EPOCH 20 - PROGRESS: at 98.13% examples, 42644 words/s, in_qsize 0, out_qsize 0
2018-05-05 06:53:42,491 : INFO : EPOCH 20 - PROGRESS: at 98.18% examples, 42645 words/s, in_qsiz

2018-05-05 06:54:47,918 : INFO : worker thread finished; awaiting finish of 5 more threads
2018-05-05 06:54:47,998 : INFO : worker thread finished; awaiting finish of 4 more threads
2018-05-05 06:54:48,033 : INFO : worker thread finished; awaiting finish of 3 more threads
2018-05-05 06:54:48,090 : INFO : worker thread finished; awaiting finish of 2 more threads
2018-05-05 06:54:48,111 : INFO : worker thread finished; awaiting finish of 1 more threads
2018-05-05 06:54:48,155 : INFO : worker thread finished; awaiting finish of 0 more threads
2018-05-05 06:54:48,156 : INFO : EPOCH - 20 : training on 268643771 raw words (83321505 effective words) took 1952.7s, 42669 effective words/s
2018-05-05 06:54:48,157 : INFO : training on a 5372875420 raw words (1666530415 effective words) took 53487.7s, 31157 effective words/s


CPU times: user 1d 13h 45min 48s, sys: 22min 37s, total: 1d 14h 8min 26s
Wall time: 14h 57min 16s


In [13]:
model.save('py_models/FT_CBOW')

2018-05-05 06:55:04,159 : INFO : saving FastText object under py_models/FT_CBOW, separately None
2018-05-05 06:55:04,200 : INFO : storing np array 'vectors' to py_models/FT_CBOW.wv.vectors.npy
2018-05-05 06:55:04,393 : INFO : not storing attribute buckets_word
2018-05-05 06:55:04,394 : INFO : storing np array 'vectors_ngrams' to py_models/FT_CBOW.wv.vectors_ngrams.npy
2018-05-05 06:55:04,804 : INFO : not storing attribute vectors_norm
2018-05-05 06:55:04,805 : INFO : not storing attribute vectors_ngrams_norm
2018-05-05 06:55:04,806 : INFO : storing np array 'vectors_vocab' to py_models/FT_CBOW.wv.vectors_vocab.npy
2018-05-05 06:55:05,421 : INFO : not storing attribute vectors_vocab_norm
2018-05-05 06:55:05,423 : INFO : storing np array 'syn1neg' to py_models/FT_CBOW.trainables.syn1neg.npy
2018-05-05 06:55:05,968 : INFO : storing np array 'syn1' to py_models/FT_CBOW.trainables.syn1.npy
2018-05-05 06:55:06,585 : INFO : storing np array 'vectors_ngrams_lockf' to py_models/FT_CBOW.trainabl

In [14]:
model = gensim.models.Word2Vec.load('py_models/FT_CBOW')

2018-05-05 06:55:14,233 : INFO : loading Word2Vec object from py_models/FT_CBOW
2018-05-05 06:55:18,364 : INFO : loading vocabulary recursively from py_models/FT_CBOW.vocabulary.* with mmap=None
2018-05-05 06:55:18,365 : INFO : loading wv recursively from py_models/FT_CBOW.wv.* with mmap=None
2018-05-05 06:55:18,365 : INFO : loading vectors from py_models/FT_CBOW.wv.vectors.npy with mmap=None
2018-05-05 06:55:19,391 : INFO : loading vectors_ngrams from py_models/FT_CBOW.wv.vectors_ngrams.npy with mmap=None
2018-05-05 06:55:24,842 : INFO : loading vectors_vocab from py_models/FT_CBOW.wv.vectors_vocab.npy with mmap=None
2018-05-05 06:55:26,470 : INFO : setting ignored attribute buckets_word to None
2018-05-05 06:55:26,471 : INFO : setting ignored attribute vectors_norm to None
2018-05-05 06:55:26,472 : INFO : setting ignored attribute vectors_ngrams_norm to None
2018-05-05 06:55:26,474 : INFO : setting ignored attribute vectors_vocab_norm to None
2018-05-05 06:55:26,484 : INFO : loading 

In [ ]:
# x.doesnt_match(words)

# #     Which word from the given list doesn’t go with the others?
# #     Parameters:	words – List of words
# #     Returns:	The word further away from the mean of all words.
# #     Return type:	str

# x.index2word
# ### list of words in the sorted order of their frequency 

# y = x.vocab['parti']
# y.count
# # find freq. of any word


# x.most_similar_cosmul(positive=None, negative=None, topn=10)
# # Find the top-N most similar words, using the multiplicative combination objective proposed by 
# # Omer Levy and Yoav Goldberg.Positive words still contribute positively towards the similarity, negative words 
# # negatively, but with less susceptibility to one large distance dominating the calculation.

# x.most_similar_to_given(entity1, entities_list)
# #    Return the entity from entities_list most similar to entity1.

# x.n_similarity(ws1, ws2)
# #Compute cosine similarity between two sets of words


# x.similar_by_vector(x['fit'], topn=10, restrict_vocab=None)
# # closest vectors
# # if topn is False, similar_by_vector returns the vector of similarity scores.

# x.similar_by_word(word, topn=10, restrict_vocab=None)
# #  Find the top-N most similar words.

# x.similarity(w1, w2)
# #Compute cosine similarity between two words.

# x.wmdistance(doc1, doc2)
# # word movers distance

# y = x.vocab['parti']
# y.count
# #freq in corpus

In [16]:
%%time

import math
from six import iteritems
from six.moves import xrange
idf = {}
for word, freq in dictionary.dfs.iteritems():
    idf[dictionary[word]] = math.log(dictionary.num_docs) - math.log(freq)


CPU times: user 276 ms, sys: 28 ms, total: 304 ms
Wall time: 290 ms


In [17]:
# get the query truth in dictionary
query_truth = {}
for i in range(1,11):
    query_truth[str(i)]=[]
    
    
f = open('LegalAdhocTask/Consumer.qrels')
lines = [line.rstrip('\n').split("\t") for line in f]
for line in lines:
    del line[1]
    query_truth[line[0]].append(line[1:])


In [18]:
w2v = model.wv
def vec(document):
    return np.add.reduce([idf[i]*w2v[i] for i in document if i in dictionary.token2id])

In [19]:
%%time
doc_vec = []
for x in iter_token_corpus():
    x = vec(x)
    doc_vec.append(x)

CPU times: user 45min 3s, sys: 11.9 s, total: 45min 15s
Wall time: 55min 17s


In [20]:
from scipy.spatial.distance import cosine
def get_scores(query):
    scores = []
    i = 0
    query = vec(query)
    for x in doc_vec:
        if isinstance(x, np.ndarray):
            score = 1 - cosine(x, query)
        else:
            score = -1000
        scores.append(score)
    return scores

In [21]:
%%time
results = copy.deepcopy(query_truth)

sim_list = [0]
rank_list = [0]
queries = [0]
for i,query in enumerate(files_to_tokens('LegalAdhocTask/q*.txt')):
    queries.append(query)
    sims = get_scores(query)
    sim_list.append(sims)
    # rank of every document wrt similarity
    ranks = rankdata(sims, method='ordinal')
    ranks= len(ranks)+1 - ranks 
    rank_list.append(ranks)
    
    # update the query truth tuples with similarity score and the ranks
    for x in results[str(i+1)]:
        x.append(sims[filenames.index(x[0]+'.txt')])
        x.append(ranks[filenames.index(x[0]+'.txt')])
        

CPU times: user 2min 45s, sys: 1.71 s, total: 2min 47s
Wall time: 2min 58s


In [22]:
results

{'1': [['ConsumerCourt_DCDRC_100385', '1', 0.4536736011505127, 2459],
  ['ConsumerCourt_DCDRC_106530', '0', 0.2565425932407379, 20000],
  ['ConsumerCourt_DCDRC_107608', '1', 0.4783153235912323, 1752],
  ['ConsumerCourt_DCDRC_114291', '1', 0.5272611379623413, 741],
  ['ConsumerCourt_DCDRC_114382', '1', 0.5232726335525513, 807],
  ['ConsumerCourt_DCDRC_118185', '1', 0.531554102897644, 682],
  ['ConsumerCourt_DCDRC_130318', '0', 0.5109704732894897, 1036],
  ['ConsumerCourt_DCDRC_130570', '1', 0.5510963201522827, 437],
  ['ConsumerCourt_DCDRC_131146', '1', 0.5930391550064087, 152],
  ['ConsumerCourt_DCDRC_131717', '1', 0.5762718319892883, 242],
  ['ConsumerCourt_DCDRC_131741', '1', 0.539059579372406, 588],
  ['ConsumerCourt_DCDRC_131818', '1', 0.5574231743812561, 381],
  ['ConsumerCourt_DCDRC_131950', '0', 0.5228097438812256, 815],
  ['ConsumerCourt_DCDRC_131972', '0', 0.612556517124176, 82],
  ['ConsumerCourt_DCDRC_132932', '0', 0.6368710994720459, 25],
  ['ConsumerCourt_DCDRC_133592', '1

In [23]:
model_name = 'FT_CBOW_IDF'

with open('py_results/' + model_name + 'sim_list.pkl', 'wb') as output:
    pickle.dump(sim_list, output, pickle.HIGHEST_PROTOCOL)
with open('py_results/' + model_name + 'rank_list.pkl', 'wb') as output:
    pickle.dump(rank_list, output, pickle.HIGHEST_PROTOCOL)


In [24]:
# Store results in 1st sheet


wb = Workbook()
dest_filename = 'result_excel/' + model_name + '.xlsx'
ws1 = wb.active
ws1.title = "ground_truth"
ws1.append(['Query','Filename', 'Relevance', 'Score', 'Rank'])
for key,value in results.iteritems():
    for i in value:
        ws1.append([int(key)]+ i)

wb.save(filename = dest_filename)

#Query wise (F score)

import pandas as pd

f = pd.ExcelFile(dest_filename)

from scipy.stats import hmean



places = 4
wb = load_workbook(dest_filename)
ws1 = wb.create_sheet(title="evaluation_Qwise")

ws1.append(['Query','Docs considered', 'Precision/Recall', 'Model', 1, 5 ,10, 25, 50, 100, 500, 1000])

k = [1.0, 5.0 ,10.0, 25.0, 50.0, 100.0, 500.0, 1000.0]
for sheet in f.sheet_names:
    if(sheet == "evaluation"):
        continue
    for q in np.arange(1,11):

        x = f.parse(sheet)
        x = x[x['Query'] == q]
        total_1 = (float)(x[x['Relevance'] == 1].shape[0])
        total_0 = (float)(x[x['Relevance'] == 0].shape[0])
        total = (float)(x.shape[0])
        
        ####  repitition due to complication in considering both 1 & 0 relevance
        # precision 1
        row = [q, 1, 'P', model_name ]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 1 , x['Rank'] <= i)].shape[0]/i)
        ws1.append(row);
        p1 = row;
        # precision 0
        row = [q, 0, 'P', model_name ]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 0 , x['Rank'] <= i)].shape[0]/i)    
        ws1.append(row);
        p0 = row;
        #precision 10
        row = [q, 10, 'P', model_name]
        for i in k:
            row.append(x[x['Rank'] <= i].shape[0]/i)  
        ws1.append(row);
        p10 = row;  
        
        
        # recall 1
        row = [q, 1, 'R', model_name]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 1 , x['Rank'] <= i)].shape[0]/total_1)
            row[-1] = round(row[-1],places)
        ws1.append(row);
        r1 = row;    
        # recall 0
        row = [q, 0, 'R', model_name ]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 0 , x['Rank'] <= i)].shape[0]/total_0)
            row[-1] = round(row[-1],places)
        ws1.append(row);
        r0 = row;
        #recall 10
        row = [q, 10, 'R', model_name ]
        for i in k:
            row.append(x[x['Rank'] <= i].shape[0]/total)
            row[-1] = round(row[-1],places)
        ws1.append(row);
        r10 = row;      


        # F 1
        row = [q, 1, 'F', model_name ]
        for i in range(-len(k), 0, 1):
            if p1[i] == 0.0 :
                row.append(0.0)
            else:
                row.append(hmean([p1[i],r1[i]]))
            row[-1] = round(row[-1],places)
        ws1.append(row);

        # F 0
        row = [q, 0, 'F', model_name]
        for i in range(-len(k), 0, 1):
            if p0[i] == 0.0:
                row.append(0.0)
            else:
                row.append(hmean([p0[i],r0[i]]))
            row[-1] = round(row[-1],places)
        ws1.append(row);

        # F 10
        row = [q, 10, 'F', model_name]
        for i in range(-len(k), 0, 1):
            if p10[i] == 0.0:
                row.append(0.0)
            else:
                row.append(hmean([p10[i],r10[i]]))
            row[-1] = round(row[-1],places)
        ws1.append(row);
        
wb.save(filename = dest_filename)


#Query wise Average precision
# precision sum
def p_sum(z):
    z = z.copy()  
    z.sort_values(inplace=True)
    result = 0
    for i,val in enumerate(z):
        result += (i+1)/float(val) 
    return result


import pandas as pd

f = pd.ExcelFile(dest_filename)

from scipy.stats import hmean


places = 4
wb = load_workbook(dest_filename)
ws1 = wb.create_sheet(title="AP_Qwise")

ws1.append(['Query','Docs considered', 'Precision/Recall', 'Model', 1, 5 ,10, 25, 50, 100, 500, 1000])


for sheet in f.sheet_names:    
    if(sheet == "evaluation"or sheet == "evaluation_Qwise"):
        continue
    for q in np.arange(1,11):
        x = f.parse(sheet)
        x = x[x['Query'] == q]
        total = {}
        total[1] = (float)(x[x['Relevance'] == 1].shape[0])
        total[0] = (float)(x[x['Relevance'] == 0].shape[0])
        total[10] = (float)(x.shape[0])
        
        for rel in [1,0]:
            # precision 1
            row = [q, rel, 'AP', model_name ]
            for i in [1.0, 5.0, 10.0, 25.0, 50.0, 100.0, 500.0, 1000.0]:
                row.append(p_sum(x[np.logical_and(x['Relevance'] == rel, x['Rank'] <= i)]['Rank'])/total[rel])
            ws1.append(row);

        row = [q, 10, 'AP', model_name ]
        for i in [1.0, 5.0, 10.0, 25.0, 50.0, 100.0, 500.0, 1000.0]:
            row.append(p_sum(x[x['Rank'] <= i]['Rank'])/total[10])
        ws1.append(row);
wb.save(filename = dest_filename)

In [26]:
def append_df_to_excel(filename, df, sheet_name='Sheet1', startrow=None,
                       truncate_sheet=False, 
                       **to_excel_kwargs):
    """
    Append a DataFrame [df] to existing Excel file [filename]
    into [sheet_name] Sheet.
    If [filename] doesn't exist, then this function will create it.

    Parameters:
      filename : File path or existing ExcelWriter
                 (Example: '/path/to/file.xlsx')
      df : dataframe to save to workbook
      sheet_name : Name of sheet which will contain DataFrame.
                   (default: 'Sheet1')
      startrow : upper left cell row to dump data frame.
                 Per default (startrow=None) calculate the last row
                 in the existing DF and write to the next row...
      truncate_sheet : truncate (remove and recreate) [sheet_name]
                       before writing DataFrame to Excel file
      to_excel_kwargs : arguments which will be passed to `DataFrame.to_excel()`
                        [can be dictionary]

    Returns: None
    """
    from openpyxl import load_workbook

    # ignore [engine] parameter if it was passed
    if 'engine' in to_excel_kwargs:
        to_excel_kwargs.pop('engine')

    writer = pd.ExcelWriter(filename, engine='openpyxl')

    try:
        # try to open an existing workbook
        writer.book = load_workbook(filename)

        # get the last row in the existing Excel sheet
        # if it was not specified explicitly
        if startrow is None and sheet_name in writer.book.sheetnames:
            startrow = writer.book[sheet_name].max_row

        # truncate sheet
        if truncate_sheet and sheet_name in writer.book.sheetnames:
            # index of [sheet_name] sheet
            idx = writer.book.sheetnames.index(sheet_name)
            # remove [sheet_name]
            writer.book.remove(writer.book.worksheets[idx])
            # create an empty sheet [sheet_name] using old index
            writer.book.create_sheet(sheet_name, idx)

        # copy existing sheets
        writer.sheets = {ws.title:ws for ws in writer.book.worksheets}
    except FileNotFoundError:
        # file does not exist yet, we will create it
        pass

    if startrow is None:
        startrow = 0

    # write out the new sheet
    df.to_excel(writer, sheet_name, startrow=startrow, index= False, header = False, **to_excel_kwargs)

    # save the workbook
    writer.save()

    
f = pd.ExcelFile(dest_filename)
sec_dest = 'result_excel/all_results.xlsx'
f2 = pd.ExcelFile(sec_dest)
append_df_to_excel(sec_dest, f.parse(1), sheet_name= f2.sheet_names[0])
append_df_to_excel(sec_dest, f.parse(2), sheet_name= f2.sheet_names[1])

In [ ]:
############################################################

In [ ]:
def Top_x(x, R):
    R = list(R)
    x_names = []
    for i in range(x):
        x_names.append(filenames[R.index(i + 1)].strip('.txt'))
    return x_names
    
    

In [ ]:
def score_stat(word, freq, index):
    index_doc = dict(bm25.corpus[index])
    word = dictionary.doc2bow([word])[0][0]
    idf = bm25.idf[word] if bm25.idf[word] >= 0 else EPSILON * average_idf
    score = freq*((idf * index_doc[word] * (PARAM_K1 + 1)
              / (index_doc[word] + PARAM_K1 * (1 - PARAM_B + PARAM_B * doc_len[index] / bm25.avgdl))))
    return (index_doc[word], score)

In [ ]:
wb = Workbook()
dest_filename = 'Temp.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)
def common_words(q, F):
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    index = filenames.index(F + '.txt')
    index_doc = dict(bm25.corpus[index])
    row = []
    for word, freq in  zip(q_words, q_freq):
        w = dictionary.doc2bow([word])[0][0]
        if w in index_doc: 
            f, s = score_stat(word, freq, index)
            row.append([word + ', ' + str(round(bm25.idf[w], 2)), freq, f,  round( (s*100)/sim_list[q][index], 1)])  
    row.sort(key = lambda x: (x[3],x[1],x[2]), reverse = True)
    wb = load_workbook('Temp.xlsx')
    ws = wb.create_sheet(title=str(q) + F)
    ws.append(['word,idf', 'Query freq', 'freq', '% score'])
    for i in row:
        ws.append(i)
    wb.save(filename = 'Temp.xlsx')


In [ ]:
f = open("toberead.txt", 'r') 
count = 0
q = 1
for i in f:
    if i == '\n':
        continue
    count = count + 1
    common_words(q, i.strip())
    if count % 5 == 0:
        q = q + 1


In [ ]:
for i in files_to_tokens(full_filenames[filenames.index(doc + '.txt')]):
    for j in i:
        print j

In [ ]:
doc = 'ConsumerCourt_SCDRC_30176'
corpus[]

In [ ]:
common_words(1, 'ConsumerCourt_DCDRC_41588')

In [ ]:
df = pd.DataFrame(index= None, columns=['words','pair'])


In [ ]:
df

In [ ]:
print df

In [ ]:
df.append(['lol', ('we','wew')])

In [ ]:
def uncommon_words(q, filename)

In [ ]:
# Store results in 1st sheet
wb = Workbook()
dest_filename = 'Explore_BM25.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)

wb = load_workbook('Explore_BM25.xlsx')

for q in range(1, 11):
    ws = wb.create_sheet(title="q" + str(q))
    #x_names = Top_x(10, rank_list[q])
    top_row = ['Doc Name', 'Rel', 'Doc Length', ' Rank', 'Score']
    sec_row = [' ']*5
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    ws.append(top_row + [i[0]  for i in temp])
    ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    
    #continue
    doc_list = [i[0] for i in query_truth[str(q)]] + Top_x(10, rank_list[q])
    doc_list = list((set(doc_list)))
    doc_list.sort(key = lambda doc : rank_list[q][filenames.index(doc + '.txt')])
    doc_row = []
    for doc in doc_list:
        temp  = [doc]
        rel_dic = dict(query_truth[str(q)])
        if doc in rel_dic:
            temp.append(rel_dic[doc])
        else:
            temp.append('Not')
        temp.append(doc_len[filenames.index(doc + '.txt')])
        temp.append(rank_list[q][filenames.index(doc + '.txt')])
        temp.append(round(sim_list[q][filenames.index(doc + '.txt')], 2))
        doc_row.append(temp)

    for row in doc_row:
        index = filenames.index(row[0] + '.txt')
        index_doc = dict(bm25.corpus[index])
        
        for word, freq in  zip(q_words, q_freq):
            if dictionary.doc2bow([word])[0][0] in index_doc: 
                f, s = score_stat(word, freq, index)
                row.append( str(f) + ', ' +  str(round( (s*100)/sim_list[q][index], 1) ))
            else:
                row.append('X')
        ws.append(row)
        ws.append([])        
wb.save(filename = dest_filename)

In [ ]:
# Store results in 1st sheet
wb = Workbook()
dest_filename = 'Explore_BM25_uncom.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)



wb = load_workbook('Explore_BM25_uncom.xlsx')

for q in range(1, 11):
    ws = wb.create_sheet(title="q" + str(q))
    #x_names = Top_x(10, rank_list[q])
    top_row = ['Doc Name', 'Rel', 'Doc Length', ' Rank', 'Score']
    sec_row = [' ']*5
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    ws.append(top_row + [i[0]  for i in temp])
    ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    
    #continue
    doc_list = [i[0] for i in query_truth[str(q)]] + Top_x(10, rank_list[q])
    doc_list = list((set(doc_list)))
    doc_list.sort(key = lambda doc : rank_list[q][filenames.index(doc + '.txt')])
    doc_row = []
    for doc in doc_list:
        temp  = [doc]
        rel_dic = dict(query_truth[str(q)])
        if doc in rel_dic:
            temp.append(rel_dic[doc])
        else:
            temp.append('Not')
        temp.append(doc_len[filenames.index(doc + '.txt')])
        temp.append(rank_list[q][filenames.index(doc + '.txt')])
        temp.append(round(sim_list[q][filenames.index(doc + '.txt')], 2))
        doc_row.append(temp)

    for row in doc_row:
        index = filenames.index(row[0] + '.txt')
        index_doc = dict(bm25.corpus[index])
        
#         for word, freq in  zip(q_words, q_freq):
#             if dictionary.doc2bow([word])[0][0] in index_doc: 
#                 f, s = score_stat(word, freq, index)
#                 row.append( str(f) + ', ' +  str(round( (s*100)/sim_list[q][index], 1) ))
#             else:
#                 row.append('X')
        #ws.append(row)
        
        sec_row = [' ']*5
        temp = []
        for word, freq in index_doc.iteritems():
            if dictionary[word] not in q_words:
                temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
        ws.append(row + [i[0]  for i in temp])
        ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
        ws.append([])        
wb.save(filename = dest_filename)

In [ ]:
# Store results in 1st sheet
wb = Workbook()
dest_filename = 'Explore_BM25_all.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)



wb = load_workbook('Explore_BM25_all.xlsx')

for q in range(1, 11):
    ws = wb.create_sheet(title="q" + str(q))
    #x_names = Top_x(10, rank_list[q])
    top_row = ['Doc Name', 'Rel', 'Doc Length', ' Rank', 'Score']
    sec_row = [' ']*5
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    ws.append(top_row + [i[0]  for i in temp])
    ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    
    #continue
    doc_list = [i[0] for i in query_truth[str(q)]] + Top_x(10, rank_list[q])
    doc_list = list((set(doc_list)))
    doc_list.sort(key = lambda doc : rank_list[q][filenames.index(doc + '.txt')])
    doc_row = []
    for doc in doc_list:
        temp  = [doc]
        rel_dic = dict(query_truth[str(q)])
        if doc in rel_dic:
            temp.append(rel_dic[doc])
        else:
            temp.append('Not')
        temp.append(doc_len[filenames.index(doc + '.txt')])
        temp.append(rank_list[q][filenames.index(doc + '.txt')])
        temp.append(round(sim_list[q][filenames.index(doc + '.txt')], 2))
        doc_row.append(temp)

    for row in doc_row:
        index = filenames.index(row[0] + '.txt')
        index_doc = dict(bm25.corpus[index])
        
        for word, freq in  zip(q_words, q_freq):
            if dictionary.doc2bow([word])[0][0] in index_doc: 
                f, s = score_stat(word, freq, index)
                row.append( str(f) + ', ' +  str(round( (s*100)/sim_list[q][index], 1) ))
            else:
                row.append('X')
        ws.append(row)
        
        sec_row = [' ']*5
        temp = []
        for word, freq in index_doc.iteritems():
            if dictionary[word] not in q_words:
                temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
        ws.append(sec_row + [i[0]  for i in temp])
        ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
        ws.append([])        
wb.save(filename = dest_filename)